# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Темур Холматов`

Группа: `MADE-DS-32`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [1]:
from IPython.display import clear_output

In [2]:
# !pip install OSMPythonTools
# !pip install geopandas
# !pip install osmapi
# !pip install folium
# !pip install openrouteservice
# !sudo apt install python3-rtree
# !pip install "rtree>=0.8,<0.9"
# clear_output(wait=True)

In [3]:
from OSMPythonTools.nominatim import Nominatim
from osmapi import OsmApi
from OSMPythonTools.overpass import overpassQueryBuilder, Overpass
import folium
from folium.plugins import TimestampedGeoJson
from shapely.geometry import Polygon, Point, MultiPolygon, LineString
from shapely.geometry import shape, mapping
from OSMPythonTools.overpass import overpassQueryBuilder, Overpass
import random
from sklearn.metrics.pairwise import haversine_distances
from math import radians, degrees
import pyproj
import time
import warnings
warnings.filterwarnings("ignore")

In [4]:
nominatim = Nominatim()
areaId = nominatim.query('Afganistan').areaId()
overpass = Overpass()
query = overpassQueryBuilder(area=areaId, elementType=['relation'], selector='"admin_level"="2"', includeGeometry=True)
result = overpass.query(query)
countryGeometry = result.elements()[0].geometry()

In [5]:
random.seed(20)

def haversine_distance(p1, p2):
    p1_coords = [radians(p) for p in list(p1.coords[0])]
    p2_coords = [radians(p) for p in list(p2.coords[0])]
    return haversine_distances([p1_coords, p2_coords])[0,1] * 6371000

def generate_random_point(dist_points):
    while True:
        point = Point(random.uniform(-85, 85), random.uniform(-180, 180))
        ok = True
        for d, p in dist_points:
            if haversine_distance(p, point) <= d:
                ok = not ok
                break
        if ok:
            return point

def solve(country):
    # lon-lat -> lat-lon
    country = Polygon([(coords[1], coords[0]) for coords in country.exterior.coords])
    dist_points = []
    while True:
        point = generate_random_point(dist_points)
        if country.contains(point):
            return point, dist_points
        min_dist = None
        pmd = None
        for poly_point in country.exterior.coords:
            dist = haversine_distance(point, Point(*poly_point))
            if min_dist is None or dist < min_dist:
                min_dist = dist
                pmd = poly_point
        dist_points.append((min_dist, point))


def get_circle(point, dist):
    srcProj = pyproj.Proj(init='EPSG:4326')
    dstProj = pyproj.Proj(proj='utm', zone=10, ellps='WGS84', preserve_units=False)
    x, y = pyproj.transform(srcProj, dstProj, point.coords[0][1], point.coords[0][0])
    point = Point(x, y)
    circle = point.buffer(dist)
    buffer_points =  [coords for coords in circle.exterior.coords]
    proj_buffer_points = []
    for point in buffer_points:
        x = point[0]
        y = point[1]
        x, y = pyproj.transform(dstProj, srcProj, x, y)
        proj_buffer_points.append((y, x))
    return Polygon(proj_buffer_points)

afganistan = shape(countryGeometry)
target_point, points = solve(afganistan)

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

In [18]:
m = folium.Map(location=[25.1652, 23.2031], zoom_start=2, width='80%', height='80%')
folium.GeoJson(
    countryGeometry,
    name='geojson'
).add_to(m)

folium.Marker(
    list(target_point.coords[0]),
    popup=f'Point in Afganistan',
    icon=folium.Icon(color='green')
).add_to(m)

data = {"type": "FeatureCollection",
        "features": []}
start_tp, time_step = 1435708800000, 86400000
for i, (d, p) in enumerate(points):
    data['features'].append({
        'type': 'Feature',
        'geometry': {
            'type': 'Point',
            'coordinates': p.coords[0][::-1]
        },
        'properties': {
            'times': [start_tp + i * time_step]
        }
    })

    circle = [[coords[1], coords[0]] for coords in get_circle(p, d).exterior.coords]
    swap_pos = 0
    max_dist = abs(circle[0][0]-circle[-1][0])
    for j in range(1, len(circle)):
        dist = abs(circle[j][0]-circle[j-1][0])
        if dist > max_dist:
            max_dist = dist
            swap_pos = j
    circle = circle[swap_pos:] + circle[:swap_pos]

    data['features'].append({
        'type': 'Feature',
        'geometry': {
            'type': 'LineString',
            'coordinates': circle
        },
        'properties': {
            'times': [start_tp + i * time_step]*len(circle)
        }
    })

TimestampedGeoJson(data, transition_time=1000, add_last_point=False, loop=False).add_to(m)


m

Идея заключается в том, чтобы удалять из пространства допустимых значений для рандомных точек области, в которых Афганистан точно не находится. Таким образом можно сужать пространство довольно быстро. Однако, здесь есть свои подводные камни. Дело в том, что нет готового функционала для генерации точек в полигоне, поэтому приходится при каждой генерации точки проверять их на вхождение в допустимое пространство. 

P.S: на иллюстрации примерно очерчены границы буферов точек, внутри которых точно не будет находится Афганистан.

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

In [6]:
from rtree import index
from tqdm import tqdm 

In [7]:
target_point.coords[0]

(35.294994971386515, 66.2109461875516)

In [8]:
overpass = Overpass()
result = overpass.query('relation["admin_level"="2"][boundary=administrative];out;')

In [9]:
country_names = []
for e in result.elements():
    if ' - ' not in e.tags()['name:en']:
        country_names.append(e.tags()['name:en'])
print('Number of countries:', len(country_names))

Number of countries: 221


In [10]:
area_ids = {}
nom = Nominatim()
for country_name in tqdm(country_names, position=0, leave=True):
    country = nom.query(country_name)
    area_ids[country_name] = country.areaId()
    time.sleep(0.8)
    clear_output(wait=True)

100%|██████████| 221/221 [02:58<00:00,  1.24it/s]


In [11]:
area_ids = {name: area_id for name, area_id in area_ids.items() if area_id is not None and area_id % 10 == 0}
area_ids.keys()

dict_keys(['Brazil', 'Estonia', 'Australia', 'Eswatini', 'Bangladesh', 'Syria', 'Liberia', 'Central African Republic', 'Ethiopia', 'Cameroon', 'Tanzania', 'Malawi', 'Uzbekistan', 'Honduras', 'Portugal', 'Azerbaijan', 'Comoros', 'São Tomé and Príncipe', 'Antigua and Barbuda', 'Monaco', 'Kosovo', 'Brunei', 'Tokelau', 'Norway'])

In [26]:
def search_elements_with_rtree(result):
    idx = index.Index()
    left, bottom, right, top = (-180, -85, 180, 85)
    idx.insert(0, (left, bottom, right, top))
    
    for i, e in enumerate(result.elements()):
        geom = shape(e.geometry())
        if geom.geom_type == 'Point':
            lon, lat = geom.coords[0]
        elif geom.geom_type == 'Polygon':
            lon, lat = geom.centroid.coords[0]
        else:
            continue
        idx.insert(i, (lon, lat, lon, lat))

    rev_target = list(target_point.coords[0])[::-1]
    target_bounds = (*rev_target, *rev_target)
    close_p_idx = [idx for idx in list(idx.nearest(target_bounds, 6)) if idx != 0][:5]

    points = []
    dist_sum = 0
    for idx in close_p_idx:
        geom = shape(result.elements()[idx-1].geometry())
        if geom.geom_type == 'Point':
            lon, lat = geom.coords[0]
        elif geom.geom_type == 'Polygon':
            lon, lat = geom.centroid.coords[0]
        else:
            continue
        dist = haversine_distance(target_point, Point(lat, lon))
        dist_sum += dist
        points.append((lat, lon))
    return dist_sum, points

def exercise_1():
    best_result = {'max_count': None, 'area_id': None}
    for country in area_ids:
        area_id = area_ids[country]
        query = overpassQueryBuilder(area=area_id, elementType='way', selector='"building"="residential"', out='count')
        count = overpass.query(query, timeout=300).countElements()
        if best_result['max_count'] is None or best_result['max_count'] < count:
            best_result['max_count'] = count
            best_result['area_id'] = area_id

    query = overpassQueryBuilder(area=best_result['area_id'], elementType='node', selector='"amenity"="atm"', out='body')
    result = overpass.query(query, timeout=300) 
    return search_elements_with_rtree(result)

dist_atm, atm_points = exercise_1()

In [27]:
m = folium.Map(location=[25.1652, 23.2031], zoom_start=2, width='80%', height='80%')

folium.Marker(
    list(target_point.coords[0]),
    popup=f'Point in Afganistan',
    icon=folium.Icon(color='green')
).add_to(m)

for point in atm_points:
    folium.Marker(
        point,
        popup='ATM'
    ).add_to(m)

m

In [28]:
def exercise_2():
    best_result = {'max_count': None, 'area_id': None}
    for country in area_ids:
        area_id = area_ids[country]
        query = overpassQueryBuilder(area=area_id, elementType=['way', 'node', 'rel'], selector='"amenity"="pharmacy"', out='count')
        count = overpass.query(query, timeout=400).countElements()
        if best_result['max_count'] is None or best_result['max_count'] < count:
            best_result['max_count'] = count
            best_result['area_id'] = area_id

    query = overpassQueryBuilder(area=best_result['area_id'], elementType=['way', 'node'], selector='"amenity"="school"', includeGeometry=True, out='body')
    result = overpass.query(query, timeout=300)
    
    return search_elements_with_rtree(result)

dist_school, school_points = exercise_2()

In [29]:
m = folium.Map(location=[25.1652, 23.2031], zoom_start=2, width='80%', height='80%')

folium.Marker(
    list(target_point.coords[0]),
    popup=f'Point in Afganistan',
    icon=folium.Icon(color='green')
).add_to(m)

for point in school_points:
    folium.Marker(
        point,
        popup='School'
    ).add_to(m)

m

In [30]:
def exercise_3():
    best_result = {'max_count': None, 'area_id': None}
    for country in area_ids:
        area_id = area_ids[country]
        result = nominatim.query(country)
        min_lat, max_lat, _, _ = list(map(float, result.toJSON()[0]['boundingbox']))
        mid_lat = (min_lat + max_lat) / 2

        query1 = overpassQueryBuilder(area=area_id, elementType=['node'], selector='"highway"="bus_stop"', out='body')
        result = overpass.query(query1, timeout=400)
        bus_stops_cnt = 0
        for i, e in enumerate(result.elements()):
            lon, lat = e.geometry()['coordinates']
            if lat < mid_lat:
                bus_stops_cnt += 1
        
        query2 = overpassQueryBuilder(area=area_id, elementType=['node'], selector='"railway"~"station|platform"', out='body')
        result = overpass.query(query2, timeout=400)
        platform_cnt = 0
        for i, e in enumerate(result.elements()):
            lon, lat = e.geometry()['coordinates']
            if lat < mid_lat:
                platform_cnt += 1
        
        score = platform_cnt / max(bus_stops_cnt, 1)
        if best_result['max_count'] is None or best_result['max_count'] < score:
            if country == 'Syria':
                continue  # пропустим Сирию, так как по Сирии не находятся кинотеатры
            best_result['max_count'] = score
            best_result['area_id'] = area_id
    
    query = overpassQueryBuilder(area=best_result['area_id'], elementType=['way'], selector='"amenity"="cinema"', includeGeometry=True, out='body')
    result = overpass.query(query, timeout=300)

    return search_elements_with_rtree(result)

dist_cinema, cinema_points = exercise_3()

In [31]:
m = folium.Map(location=[25.1652, 23.2031], zoom_start=2, width='80%', height='80%')

folium.Marker(
    list(target_point.coords[0]),
    popup=f'Point in Afganistan',
    icon=folium.Icon(color='green')
).add_to(m)

for point in cinema_points:
    folium.Marker(
        point,
        popup='Cinema'
    ).add_to(m)

m

In [32]:
life_quality = dist_atm + dist_school + dist_cinema
print('Life Quality in Afganistan:', life_quality)

Life Quality in Afganistan: 111167526.4548316


## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [34]:
origin = Point(40.770284, -73.968647)
destination = Point(40.703215, -73.989581)

In [35]:
import json
import requests
import shapely.wkt as wkt
from openrouteservice import client
from tqdm import tqdm
import warnings
warnings.filterwarnings("ignore")

In [36]:
url = 'https://data.cityofnewyork.us/api/views/a3nt-yts4/rows.json'
school_json = requests.get(url).json()

In [37]:
points = []
for data in school_json['data']:
    point = wkt.loads(data[8])
    points.append(point)
print("Number of points:", len(points))

Number of points: 1992


In [58]:
map_params = {'tiles':'Stamen Toner',
              'location':([40.7348,-73.9730]),
              'zoom_start': 13}
m = folium.Map(**map_params)

for point in points:
    school_coords = point.coords[0]
    folium.Marker(list(reversed(school_coords)),
                  popup='School:<br>{0}'.format(school_coords)).add_to(m)
    
m

In [47]:
# Set up the fundamentals
api_key = 'api_key' # Individual api key
clnt = client.Client(key=api_key) # Create client with api key

In [86]:
# Request normal route between appropriate locations without schools
request_params = {'coordinates': [list(origin.coords[0])[::-1], list(destination.coords[0])[::-1]],
                'format_out': 'geojson',
                'profile': 'driving-car',
                'preference': 'recommended',
                'instructions': 'false',}
route_normal = clnt.directions(**request_params)

In [95]:
# GeoJSON style function
def style_function(color):
    return lambda feature: dict(color=color,
                              weight=3,
                              opacity=0.5)

# Create new map to start from scratch
m = folium.Map(**map_params)

folium.GeoJson(data=route_normal,
                name='Route without construction sites',
                style_function=style_function('#FF0000'),
                overlay=True).add_to(m)

# Buffer route with 0.05 degrees
route_buffer = LineString(route_normal['features'][0]['geometry']['coordinates']).buffer(0.05)
folium.GeoJson(data=mapping(route_buffer),
                name='Route Buffer',
                style_function=style_function('#FFFF00'),
                overlay=True).add_to(m)

# Plot which schools fall into the buffer Polygon
close_points = []
for point in points:
    if route_buffer.contains(point):
        folium.Marker(list(reversed(point.coords[0]))).add_to(m)
        close_points.append(point)

m

In [ ]:
# source: https://github.com/GIScience/openrouteservice-examples/blob/master/python/Avoid_ConstructionSites.ipynb
def CreateBufferPolygon(point_in, resolution=10, radius=100):    

    sr_wgs = pyproj.Proj(init='epsg:4326')
    sr_utm = pyproj.Proj(init='epsg:32632') # WGS84 UTM32N
    point_in_proj = pyproj.transform(sr_wgs, sr_utm, *point_in) # unpack list to arguments
    point_buffer_proj = Point(point_in_proj).buffer(radius, resolution=resolution) # 100 m buffer
    
    # Iterate over all points in buffer and build polygon
    poly_wgs = []
    for point in point_buffer_proj.exterior.coords:
        poly_wgs.append(pyproj.transform(sr_utm, sr_wgs, *point)) # Transform back to WGS84

    return poly_wgs

In [96]:
schools_poly = []
for point in tqdm(close_points, position=0, leave=True):
    site_coords = point.coords[0]
    
    # Create buffer polygons around school points with 100 m radius and low resolution
    school_poly_coords = CreateBufferPolygon(site_coords,
                                           resolution=2, # low resolution to keep polygons lean
                                           radius=100)
    schools_poly.append(Polygon(school_poly_coords))
    

100%|██████████| 559/559 [07:23<00:00,  1.26it/s]


In [97]:
for school_poly in schools_poly:
    school_poly_coords = [(y,x) for x,y in school_poly.exterior.coords] # Reverse coords for folium
    folium.vector_layers.Polygon(locations=school_poly_coords,
                                  color='#ffd699',
                                  fill_color='#ffd699',
                                  fill_opacity=0.2,
                                  weight=3).add_to(m)

In [98]:
# Add the school polygons to the request parameters
request_params['options'] = {'avoid_polygons': mapping(MultiPolygon(schools_poly))}
route_detour = clnt.directions(**request_params)

folium.GeoJson(data=route_detour,
                        name='Route with construction sites',
                        style_function=style_function('#00FF00'),
                        overlay=True).add_to(m)

m.add_child(folium.map.LayerControl())
m